# Lecture 18: Data Cleaning Fundamentals with pandas
## Transforming Messy Data into Analysis-Ready Datasets

**Course:** INF 605 - Introduction to Programming - Python  
**Instructor:** Prof. Rongyu Lin  
**Institution:** Quinnipiac University

### Learning Objectives
By the end of this lecture, you will be able to:
1. Detect missing data using isna(), notna(), and info()
2. Handle missing data with dropna() and fillna() strategies
3. Identify and remove duplicate rows with drop_duplicates()
4. Validate and convert data types using dtype, astype(), and to_numeric()
5. Standardize column names using rename()
6. Build complete data cleaning workflows

### Prerequisites
This lecture builds on:
- Lecture 16: pandas Series (NaN, boolean indexing, statistical methods)
- Lecture 17: pandas DataFrames (structure, indexing, filtering)
- NumPy arrays from Lectures 12-13

## Setup and Imports

We need pandas for data cleaning tools and NumPy for creating missing values (NaN). Think of these as your data cleaning toolkit - pandas provides the methods, NumPy handles special values. The standard convention is importing pandas as `pd` and NumPy as `np`, which you'll see in every data analysis script.

In [ ]:
# Standard imports for data cleaning
import pandas as pd
import numpy as np

# Display versions for reference
print(f"pandas version: {pd.__version__}")
print(f"NumPy version: {np.__version__}")

## Part 1: Introduction to Data Cleaning

### Why Real-World Data is Always Messy

Real-world data is messy due to data entry errors, system glitches, incomplete forms, and inconsistent formatting. You might see duplicate records from accidental double submissions, missing values from optional fields, mixed data types from manual entry, and inconsistent column names from different sources. The phrase "garbage in, garbage out" captures a fundamental truth: flawed input data produces meaningless results. Data cleaning typically consumes 60-80% of analysis time and is the foundation of valid conclusions.

In [ ]:
# Example of messy real-world data
# Notice: missing values, duplicate entries, inconsistent types
messy_grades = pd.DataFrame({
    'Student': ['Alice', 'Bob', 'Alice', 'Charlie', 'Diana'],
    'Test1': [85, 92, 85, np.nan, '95'],  # Mixed types!
    'Test2': [87, np.nan, 87, 90, 88],    # Missing value
    'Test3': [np.nan, 89, np.nan, 88, 92] # Missing values
})

print("Messy student grade data (typical real-world problems):")
print(messy_grades)

**What We See:** Multiple quality issues - Alice appears twice (duplicate), several NaN values (missing scores), and Test1 has '95' as string mixed with integers. Without cleaning, calculations fail, duplicates get counted twice, and missing values distort statistics.

### The Data Cleaning Workflow

Professional data cleaning follows four phases: **Detect** problems (missing values, duplicates, type errors), **Assess** scope and impact (how many rows affected, how severe), **Clean** with appropriate strategies (drop, fill, convert, standardize), and **Verify** results (ensure cleaning worked correctly). This systematic approach prevents hasty decisions and documents your reasoning for future reference.

## Part 2: Detecting Missing Data

### Understanding Missing Data

Missing data appears as NaN (Not a Number) in pandas, representing absent values. Data goes missing for legitimate reasons: sensor failures, skipped survey questions, incomplete data entry, or unavailable information. Missing data is information, not just an error - it tells you something went wrong or data wasn't collected. pandas automatically handles NaN in most operations, ignoring missing values rather than causing errors.

In [ ]:
# Create sample student grade data with missing values
grades = pd.DataFrame({
    'Student': ['Alice', 'Bob', 'Charlie', 'Diana', 'Eve'],
    'Test1': [85, 92, np.nan, 95, 88],
    'Test2': [87, np.nan, 90, 88, 91],
    'Test3': [np.nan, 89, 88, np.nan, 92]
})

print("Student grades with missing values:")
print(grades)
#重复

**What We See:** Several NaN values for missing test scores across different students. Before calculating grades, we need to detect exactly where data is missing and decide how to handle it.

### Detecting Missing Values with isna()

The `isna()` method creates a boolean DataFrame showing True for missing values and False for present values. This makes missing data patterns immediately visible. You can count missing values by summing the boolean mask (True = 1, False = 0), which quantifies the problem scope and helps you decide on handling strategies.

In [ ]:
# Create boolean mask showing where values are missing
missing_mask = grades.isna()

print("Boolean mask (True = missing, False = present):")
print(missing_mask)

# Count missing values per column
print("\nMissing values per column:")
print(grades.isna().sum())

**What Happened:** The boolean mask shows True where NaN exists. Summing reveals Test3 has the most missing data (2 values). This quantification helps assess whether it's a minor (5%) or major (40%) problem, determining our handling strategy.

### Using info() for Quick Data Overview

The `info()` method displays a compact summary showing data types, non-null counts, and memory usage all at once. It's perfect for initial data assessment when you first load a dataset. You can instantly compare non-null counts to total rows to identify missing data without separate calculations.

In [ ]:
# Get comprehensive DataFrame information
print("DataFrame information summary:")
print(grades.info())

# Calculate percentage of missing data per column
total_rows = len(grades)
missing_pct = (grades.isna().sum() / total_rows * 100)
print("\nPercentage missing per column:")
print(missing_pct)

**What Happened:** The `info()` output shows 5 total entries. Test3 has only 3 non-null (40% missing) - substantial and requiring careful consideration. Generally, if a column is more than 30% missing, you need to question whether it's usable for analysis.

### Exercise 1: Detect Missing Data

Given a DataFrame of daily temperatures for two weeks, complete these tasks:
1. Create a boolean mask showing where temperature data is missing
2. Count the total number of missing temperature readings
3. Calculate what percentage of temperature data is missing
4. Use `info()` to get a comprehensive overview

In [ ]:
# Given: Two weeks of temperature data with some sensor failures
temps = pd.DataFrame({
    'Day': ['Mon', 'Tue', 'Wed', 'Thu', 'Fri', 'Sat', 'Sun',
            'Mon', 'Tue', 'Wed', 'Thu', 'Fri', 'Sat', 'Sun'],
    'Temperature': [72, np.nan, 75, 71, np.nan, 76, 73,
                   70, 68, np.nan, 69, 72, 74, np.nan]
})

print("Temperature data:")
print(temps)

# Your code here - complete the four tasks


In [ ]:
# Solution
# 1. Create boolean mask for missing temperatures
temp_missing = temps['Temperature'].isna()
print("Missing temperature mask:")
print(temp_missing)

# 2. Count total missing readings
total_missing = temps['Temperature'].isna().sum()
print(f"\nTotal missing readings: {total_missing}")

# 3. Calculate percentage missing
pct_missing = (total_missing / len(temps) * 100)
print(f"Percentage missing: {pct_missing:.1f}%")

# 4. Use info() for comprehensive overview
print("\nComprehensive overview:")
print(temps.info())

**Solution Explanation:** We found 4 missing readings out of 14 days (28.6% missing). This is substantial - dropping all missing rows would lose a third of data, while filling might introduce bias. This demonstrates why detection and assessment come before action.

## Part 3: Handling Missing Data - dropna()

### When to Remove Missing Data

Removing missing data makes sense when: (1) missing data is minimal (< 5%), (2) missing values make analysis impossible, or (3) you have plenty of remaining data after removal. The fundamental trade-off is losing data and potentially losing information. If 3 out of 100 students have ALL scores missing, removing them preserves 97% of data. But if 50 students each miss ONE of three scores, removing all 50 loses half your data unnecessarily.

### Basic dropna() - Removing Any Missing Values

The simplest approach removes any row with at least one missing value, guaranteeing completely clean data. However, this can be too aggressive - you might lose students with 2 out of 3 test scores (enough to calculate a grade) just because one score is missing. It's a trade-off between data purity and data availability.

In [ ]:
# Student grades with scattered missing values
grades_sample = pd.DataFrame({
    'Student': ['Alice', 'Bob', 'Charlie', 'Diana', 'Eve'],
    'Test1': [85, 92, np.nan, 95, 88],
    'Test2': [87, np.nan, 90, 88, 91]
})

print("Original data:")
print(grades_sample)
print(f"Original shape: {grades_sample.shape}")

In [ ]:
# Remove rows with any missing values
clean_grades = grades_sample.dropna()

print("After dropna() - rows with ANY missing value removed:")
print(clean_grades)
print(f"New shape: {clean_grades.shape}")
print(f"\nRows removed: {len(grades_sample) - len(clean_grades)}")
print(f"Data retained: {len(clean_grades)/len(grades_sample)*100:.1f}%")

**What Happened:** We lost 40% of data (2 out of 5 students). Bob had Test1=92 and Charlie had Test2=90, but both were discarded because each had one missing value. For this dataset, basic `dropna()` is too aggressive.

### dropna(how='all') - Removing Completely Empty Rows

A more conservative approach removes only rows where ALL values are missing. This preserves partial data while eliminating truly empty records that contribute zero information. It's useful after imports or merges where completely empty rows might sneak in. This is often the first cleaning step because it's safe - you only remove genuinely useless rows.

In [ ]:
# Dataset with some completely empty rows (common after imports)
data_with_empty = pd.DataFrame({
    'A': [1, np.nan, np.nan, 4, 5],
    'B': [5, np.nan, np.nan, 8, 9],
    'C': [9, np.nan, np.nan, 12, 13]
})

print("Original with completely empty rows:")
print(data_with_empty)

In [ ]:
# Remove only completely empty rows
cleaned = data_with_empty.dropna(how='all')

print("After dropna(how='all') - only completely empty rows removed:")
print(cleaned)
print(f"\nRows removed: {len(data_with_empty) - len(cleaned)}")

**What Happened:** Rows 1 and 2 were completely empty and removed. Rows with actual data were preserved. Much less destructive than default `dropna()` - you only lose rows contributing zero information.

### dropna(subset=[]) - Selective Column Requirements

Often some columns are critical (must have data) while others are optional. The `subset` parameter specifies which columns must have data for a row to be kept. Think of it like graduation requirements: core courses are required, but electives being missing doesn't disqualify you. This lets domain knowledge guide your cleaning decisions.

In [ ]:
# Student grades where Math and English are required, Science is optional
grades_req = pd.DataFrame({
    'Student': ['Alice', 'Bob', 'Charlie', 'Diana'],
    'Math': [87, 92, np.nan, 95],
    'English': [90, 85, 92, np.nan],
    'Science': [np.nan, 88, 90, 92]
})

print("Original grades (Math/English required, Science optional):")
print(grades_req)

In [ ]:
# Keep students who have BOTH Math AND English scores
# Allow missing Science scores (it's optional)
required_courses = grades_req.dropna(subset=['Math', 'English'])

print("After dropna(subset=['Math', 'English']):")
print(required_courses)
print("\nAlice kept (has Math & English, Science missing is OK)")
print("Bob kept (has all three)")
print("Charlie removed (missing Math)")
print("Diana removed (missing English)")

**What Happened:** Charlie removed (missing required Math), Diana removed (missing required English), but Alice kept despite missing Science. The `subset` parameter implements business rules based on which columns are critical.

### Exercise 2: Strategic Use of dropna()

Given student data with various missing values, apply appropriate dropna() strategies:
1. First, remove any completely empty student records (all courses missing)
2. Then, require that students must have at least Math OR English scores
3. Count how many students were removed at each step
4. Calculate what percentage of the original data you retained

In [ ]:
# Given: Student grades with various levels of completeness
student_data = pd.DataFrame({
    'Student': ['Alice', 'Bob', 'Charlie', 'Diana', 'Eve', 'Frank'],
    'Math': [85, np.nan, np.nan, 90, np.nan, np.nan],
    'English': [88, 92, np.nan, np.nan, 95, np.nan],
    'Science': [np.nan, 87, np.nan, 91, 89, np.nan]
})

print("Original student data:")
print(student_data)
print(f"Original count: {len(student_data)} students\n")

# Your code here - complete the four tasks


In [ ]:
# Solution
original_count = len(student_data)

# Step 1: Remove completely empty records
step1 = student_data.dropna(how='all', 
                             subset=['Math', 'English', 'Science'])
print("Step 1 - After removing completely empty records:")
print(step1)
removed_step1 = original_count - len(step1)
print(f"Removed: {removed_step1} students\n")

# Step 2: Require Math OR English (keep if at least one is present)
# To require "at least one," we remove rows where BOTH are missing
step2 = step1.dropna(subset=['Math', 'English'], how='all')
print("Step 2 - After requiring Math OR English:")
print(step2)
removed_step2 = len(step1) - len(step2)
print(f"Removed: {removed_step2} additional students\n")

# Step 3 & 4: Summary statistics
total_removed = original_count - len(step2)
retained_pct = (len(step2) / original_count * 100)
print(f"Total students removed: {total_removed}")
print(f"Students retained: {len(step2)} ({retained_pct:.1f}%)")

**Solution Explanation:** Frank (all courses missing) removed in Step 1. Charlie (both Math and English missing) removed in Step 2. We retained 4 out of 6 students (66.7%). Each retained student has at least one core course, making them usable for analysis.

## Part 4: Handling Missing Data - fillna()

### When to Fill Rather Than Drop

Filling (imputation) preserves dataset size but introduces assumptions about missing values. Choose filling when: (1) missing data is substantial (>5-10%), (2) you can make reasonable assumptions based on context, or (3) maintaining dataset size is critical. The key challenge is choosing appropriate fill strategies based on data characteristics - numbers vs categories, normal vs skewed distributions, sequential vs independent observations.

### Filling with a Constant Value

The simplest strategy uses a constant value with clear meaning: zero for missing quantities, "Unknown" for missing categories, or default values from business rules. The constant fill is transparent and explicit. However, choose carefully - filling missing quiz scores with 0 makes sense if policy says "not submitted = zero credit", but filling sensor readings with 0 could be disastrous if 0 has specific scientific meaning.

In [ ]:
# Quiz scores where missing means student didn't submit
quiz_scores = pd.DataFrame({
    'Student': ['Alice', 'Bob', 'Charlie', 'Diana'],
    'Quiz1': [85, 92, np.nan, 95],
    'Quiz2': [87, np.nan, 90, 88]
})

print("Original quiz scores (NaN = not submitted):")
print(quiz_scores)

In [ ]:
# Fill missing quizzes with 0 (policy: not submitted = zero)
filled = quiz_scores.copy()
filled['Quiz1'] = filled['Quiz1'].fillna(0)
filled['Quiz2'] = filled['Quiz2'].fillna(0)

print("After filling with 0:")
print(filled)

# Calculate averages to see impact
filled['Average'] = filled[['Quiz1', 'Quiz2']].mean(axis=1)
print("\nWith calculated averages:")
print(filled)

**What Happened:** Missing scores became 0, significantly lowering those students' averages. This reflects the grading policy appropriately. However, filling with 0 would be inappropriate for temperature data (0°F is real, not "missing") or prices. Context determines appropriateness.

### Filling with Statistical Measures - Mean

For numeric data, filling with the mean is appropriate when you want to preserve overall statistics. Mean filling works best for normally distributed data with few outliers. If you don't know a specific value, the average is a reasonable guess that doesn't distort overall statistics much. However, mean filling artificially reduces variance by making everything more "average".

In [ ]:
# Temperature data with missing readings
temps = pd.DataFrame({
    'Day': ['Mon', 'Tue', 'Wed', 'Thu', 'Fri'],
    'Temperature': [72, np.nan, 75, np.nan, 69]
})

print("Original temperatures (NaN = sensor failure):")
print(temps)
print(f"Available values: {temps['Temperature'].dropna().values}")

In [ ]:
# Calculate mean from available data
temp_mean = temps['Temperature'].mean()  # Automatically ignores NaN
print(f"Mean temperature from available data: {temp_mean:.1f}°F")

# Fill missing values with mean
temps['Filled_Mean'] = temps['Temperature'].fillna(temp_mean)
print("\nAfter filling with mean:")
print(temps)

# Verify the overall average is preserved
print(f"\nNew overall mean: {temps['Filled_Mean'].mean():.1f}°F")
print("(Notice it equals the original mean - preserved!)") 

**What Happened:** The mean (72.0°F) was used to fill missing days. The overall mean is preserved exactly - this is the key property of mean filling. Reasonable for temperature data if sensor failures are random.

### Filling with Statistical Measures - Median

The median (middle value) is better than mean for skewed data or data with outliers. While mean can be pulled by extremes, median is robust and represents typical values. In salary data where most earn $40k-$60k but executives earn millions, mean might be $150k (distorted) while median is $50k (typical). Use median when you suspect outliers or skewed distributions.

In [ ]:
# Product prices with some outliers (luxury items)
prices = pd.DataFrame({
    'Product': ['A', 'B', 'C', 'D', 'E', 'F'],
    'Price': [20, 25, np.nan, 22, 200, np.nan]  # E is luxury item!
})

print("Product prices (one luxury item, two missing):")
print(prices)
print(f"\nAvailable prices: {prices['Price'].dropna().values}")

In [ ]:
# Calculate mean and median for comparison
mean_price = prices['Price'].mean()
median_price = prices['Price'].median()

print(f"Mean price: ${mean_price:.2f} (distorted by $200 luxury item)")
print(f"Median price: ${median_price:.2f} (robust to outlier)")

# Fill with median (more representative of typical prices)
prices['Filled_Median'] = prices['Price'].fillna(median_price)
print("\nAfter filling with median:")
print(prices)
print("\nMedian fill assumes missing products are typical, not luxury")

**What Happened:** Mean ($66.75) is distorted by the $200 luxury item, while median ($23.50) represents typical products. We used median because it makes more reasonable assumptions about missing values when outliers exist.

### Forward Fill and Backward Fill for Sequential Data

For sequential data (time series, sensor readings), forward fill uses the previous value and backward fill uses the next value. This assumes gradual change rather than sudden jumps. Forward fill is more common because we know the past but not the future. Only use for sequential data where order matters and neighboring values influence each other.

In [ ]:
# Daily temperatures (sequential data)
daily = pd.DataFrame({
    'Day': ['Mon', 'Tue', 'Wed', 'Thu', 'Fri'],
    'Temperature': [72, np.nan, 75, np.nan, 69]
})

print("Original daily temperatures:")
print(daily)

In [ ]:
# Forward fill - use previous day's temperature
daily['Forward_Fill'] = daily['Temperature'].fillna(method='ffill')
print("Forward fill (use previous known value):")
print(daily[['Day', 'Temperature', 'Forward_Fill']])

# Backward fill - use next day's temperature  
daily['Backward_Fill'] = daily['Temperature'].fillna(method='bfill')
print("\nBackward fill (use next known value):")
print(daily[['Day', 'Temperature', 'Backward_Fill']])

**What Happened:** Forward fill gives Tuesday 72°F (from Monday) and Thursday 75°F (from Wednesday). Backward fill uses future values. Both assume gradual change. Only meaningful for sequential data.

### Exercise 3: Choosing Appropriate Fill Strategies

Given sales data with different types of missing values, apply appropriate fill strategies:
1. Fill missing Prices with the median (prices might be skewed)
2. Fill missing Quantities with 0 (missing quantity = nothing sold)
3. Fill missing Categories with "Unknown" (missing category label)
4. Calculate the total revenue (Price × Quantity) after filling

In [ ]:
# Given: Sales data with various missing values
sales = pd.DataFrame({
    'Product': ['Widget', 'Gadget', 'Tool', 'Item', 'Device'],
    'Price': [19.99, np.nan, 29.99, 24.99, np.nan],
    'Quantity': [100, 50, np.nan, 75, 60],
    'Category': ['A', 'B', np.nan, 'A', np.nan]
})

print("Original sales data with missing values:")
print(sales)

# Your code here - complete all tasks


In [ ]:
# Solution
sales_filled = sales.copy()

# 1. Fill Price with median
price_median = sales_filled['Price'].median()
sales_filled['Price'] = sales_filled['Price'].fillna(price_median)
print(f"Median price: ${price_median:.2f}")

# 2. Fill Quantity with 0
sales_filled['Quantity'] = sales_filled['Quantity'].fillna(0)

# 3. Fill Category with "Unknown"
sales_filled['Category'] = sales_filled['Category'].fillna('Unknown')

print("\nAfter filling with appropriate strategies:")
print(sales_filled)

# 4. Calculate total revenue
sales_filled['Revenue'] = sales_filled['Price'] * sales_filled['Quantity']
total_revenue = sales_filled['Revenue'].sum()
print(f"\nTotal revenue: ${total_revenue:.2f}")

**Solution Explanation:** Price filled with median ($24.99) because prices might be skewed. Quantity filled with 0 because missing means nothing sold. Category filled with "Unknown" for honest labeling. Each strategy is tailored to the data type and business meaning.

## Part 5: Identifying and Removing Duplicates

### What are Duplicate Rows?

Duplicate rows are records representing the same entity appearing multiple times, caused by data entry errors, system glitches, or data integration issues. They distort analysis by over-counting and creating bias. The key skill is distinguishing true duplicates from legitimate repeated values - two students named "John Smith" with different IDs are NOT duplicates, but the same student ID with different name spellings ARE duplicates.

### Detecting Duplicates with duplicated()

The `duplicated()` method returns a boolean Series marking duplicate rows. By default, first occurrence is False (original) and subsequent occurrences are True (duplicates). This lets you see exactly which rows are redundant copies and is useful for understanding duplicate patterns before removal.

In [ ]:
# Student enrollment with duplicate entries
students = pd.DataFrame({
    'Name': ['Alice', 'Bob', 'Alice', 'Charlie', 'Bob'],
    'ID': [101, 102, 101, 103, 104],
    'Course': ['Math', 'English', 'Math', 'Science', 'History']
})

print("Student enrollment data:")
print(students)

In [ ]:
# Find duplicate rows (all columns identical)
dupes = students.duplicated()
print("Duplicate mask (True = duplicate, False = original/unique):")
print(dupes)

# Show which specific rows are duplicates
print("\nDuplicate rows:")
print(students[dupes])

print(f"\nTotal duplicates found: {dupes.sum()}")

**What Happened:** Row 2 is marked duplicate because it's identical to row 0 (Alice, 101, Math). Row 4 is NOT duplicate even though name "Bob" repeats - the IDs differ (102 vs 104), representing different students.

### Removing Duplicates with drop_duplicates()

The `drop_duplicates()` method removes duplicates. The `keep` parameter controls which occurrence to preserve: 'first' (default), 'last', or False (remove all occurrences). Choosing which to keep requires domain knowledge - if duplicates represent multiple submissions, keep 'first'; if they're updates, keep 'last'.

In [ ]:
# Student data with duplicate records
students_dup = pd.DataFrame({
    'Name': ['Alice', 'Bob', 'Alice', 'Charlie'],
    'ID': [101, 102, 101, 103],
    'GPA': [3.8, 3.6, 3.9, 3.7]
})

print("Original with duplicate student (Alice, different GPAs):")
print(students_dup)

In [ ]:
# Keep first occurrence of duplicates
first = students_dup.drop_duplicates(keep='first')
print("Keep first occurrence:")
print(first)

# Keep last occurrence of duplicates
last = students_dup.drop_duplicates(keep='last')
print("\nKeep last occurrence:")
print(last)

**What Happened:** Alice appears twice with different GPAs (3.8 vs 3.9). Keep 'first' preserves GPA 3.8, keep 'last' preserves GPA 3.9. Which is correct depends on whether later entries are updates or errors.

### Subset-Based Duplicate Detection

Usually you want to check if key identifier columns are identical, not all columns. The `subset` parameter specifies which columns define uniqueness. This is the professional approach: identify unique key columns (student ID, email, transaction number) and detect duplicates based on those keys. The same ID with different name spellings is a true duplicate.

In [ ]:
# Student records where ID is the unique identifier
student_records = pd.DataFrame({
    'ID': [101, 102, 101, 103, 102],
    'Name': ['Alice', 'Bob', 'Alice M.', 'Charlie', 'Robert'],
    'GPA': [3.8, 3.6, 3.9, 3.7, 3.6]
})

print("Student records (ID is unique identifier):")
print(student_records)

In [ ]:
# Find duplicates based on ID only (not full row comparison)
id_dupes = student_records.duplicated(subset=['ID'])
print("Duplicates by ID (True = same ID as earlier row):")
print(id_dupes)
print("\nDuplicate records:")
print(student_records[id_dupes])

# Remove duplicates based on ID, keep last (most recent)
unique_students = student_records.drop_duplicates(
    subset=['ID'], keep='last'
)
print("\nUnique students (by ID, keeping latest entry):")
print(unique_students)

**What Happened:** Row 2 duplicates row 0 (both ID 101) despite name difference ("Alice" vs "Alice M."). Row 4 duplicates row 1 (both ID 102) despite name difference ("Bob" vs "Robert"). By using `subset=['ID']`, we correctly identify same students with name variations.

### Exercise 4: Detecting and Removing Duplicates

Given customer transaction data with some duplicate entries:
1. Identify duplicate transactions based on TransactionID (the unique key)
2. Count how many duplicate transactions exist
3. Remove duplicates, keeping the last occurrence (assuming updates)
4. Verify that all remaining TransactionIDs are unique
5. Calculate the total revenue from unique transactions only

In [ ]:
# Given: Customer transactions with duplicates
transactions = pd.DataFrame({
    'TransactionID': ['T001', 'T002', 'T001', 'T003', 'T002', 'T004'],
    'Customer': ['Alice', 'Bob', 'Alice', 'Charlie', 'Bob', 'Diana'],
    'Amount': [50, 75, 55, 100, 75, 60]
})

print("Transaction data with duplicates:")
print(transactions)
print(f"Total transactions: {len(transactions)}\n")

# Your code here - complete all five tasks


In [ ]:
# Solution
# 1. Identify duplicates by TransactionID
dup_mask = transactions.duplicated(subset=['TransactionID'])
print("Duplicate transactions:")
print(transactions[dup_mask])

# 2. Count duplicates
dup_count = dup_mask.sum()
print(f"\nNumber of duplicate transactions: {dup_count}")

# 3. Remove duplicates, keep last
unique_trans = transactions.drop_duplicates(
    subset=['TransactionID'], keep='last'
)
print("\nUnique transactions (keeping last):")
print(unique_trans)

# 4. Verify uniqueness
final_count = len(unique_trans)
unique_ids = unique_trans['TransactionID'].nunique()
print(f"\nFinal transaction count: {final_count}")
print(f"Unique TransactionIDs: {unique_ids}")
print(f"All IDs unique? {final_count == unique_ids}")

# 5. Calculate revenue from unique transactions
total_revenue = unique_trans['Amount'].sum()
print(f"\nTotal revenue (unique transactions only): ${total_revenue}")

**Solution Explanation:** Found 2 duplicate transactions. T001 has different amounts ($50 vs $55) - keeping 'last' assumes $55 is a correction. After removing duplicates, revenue is $290 (correct), versus $420 if duplicates were included. This demonstrates why duplicate detection is critical for accurate analysis.

## Part 6: Data Type Validation and Conversion

### Why Data Types Matter

Data types determine what operations are possible. Numbers stored as strings can't be summed (you get concatenation instead of addition). Dates as strings can't be sorted chronologically. Think of data types as the vocabulary your analysis speaks - if prices are strings like "$19.99", pandas can't calculate averages until you convert to numeric types (float64). Always validate types after loading external data.

### Checking Current Data Types

Before converting, check current types using `dtypes` attribute or `info()` method. Common problems: 'object' dtype for numeric columns, mixed types forcing 'object', leading zeros in numbers, currency symbols preventing numeric interpretation. The earlier you catch type problems, the easier to fix.

In [ ]:
# Sales data with type problems (common after CSV import)
sales_types = pd.DataFrame({
    'Product': ['Widget', 'Gadget', 'Tool'],
    'Price': ['19.99', '29.99', '24.99'],  # Should be float!
    'Quantity': [100, 50, 75],
    'InStock': ['True', 'False', 'True']   # Should be bool!
})

print("Sales data:")
print(sales_types)

In [ ]:
# Check data types to identify problems
print("Data types:")
print(sales_types.dtypes)

# Try to calculate - will fail or give wrong results!
print("\nAttempting to calculate average price...")
print(f"Result: {sales_types['Price'].sum()}")
print("Problem: String concatenation instead of addition!")

**What Happened:** Price is 'object' (string), not 'float64'. Summing produces string concatenation ("19.9929.9924.99") instead of mathematical addition (74.97). This shows why type validation matters.

### Converting Types with astype()

For clean data, `astype()` directly converts to a specified type. It's fast and straightforward when you know all values are valid. However, `astype()` is strict - if even one value can't convert, the entire operation fails. Use for already-cleaned data, not as a first attempt on messy data.

In [ ]:
# Create clean sales data for conversion
sales_clean = pd.DataFrame({
    'Product': ['Widget', 'Gadget', 'Tool'],
    'Price': ['19.99', '29.99', '24.99'],
    'Quantity': ['100', '50', '75'],
    'InStock': ['True', 'False', 'True']
})

print("Original types:")
print(sales_clean.dtypes)

In [ ]:
# Convert to appropriate types
sales_clean['Price'] = sales_clean['Price'].astype(float)
sales_clean['Quantity'] = sales_clean['Quantity'].astype(int)
sales_clean['InStock'] = sales_clean['InStock'].astype(bool)

print("After type conversion:")
print(sales_clean.dtypes)

# Now calculations work correctly!
print("\nCalculations now work:")
print(f"Average price: ${sales_clean['Price'].mean():.2f}")
print(f"Total quantity: {sales_clean['Quantity'].sum()}")

**What Happened:** After conversion, types are correct (float64, int64, bool) and mathematical operations work. We can now calculate averages and sums correctly.

### Safe Conversion with to_numeric()

Real-world data is rarely clean enough for `astype()`. The `to_numeric()` function with `errors='coerce'` handles failures gracefully by converting invalid values to NaN instead of crashing. This is the professional approach: attempt conversion, coerce failures to NaN, then decide how to handle those NaN values.

In [ ]:
# Messy price data with non-numeric values
messy_prices = pd.DataFrame({
    'Item': ['Widget', 'Gadget', 'Tool', 'Device'],
    'Price': ['19.99', 'Call', '29.99', '24.99']
})

print("Messy price data:")
print(messy_prices)

In [ ]:
# Safe conversion - failures become NaN
messy_prices['Price'] = pd.to_numeric(
    messy_prices['Price'], errors='coerce'
)

print("After safe conversion:")
print(messy_prices)

# Identify which values failed conversion
failed = messy_prices['Price'].isna()
print("\nValues that failed conversion:")
print(messy_prices[failed])

# Calculate statistics on successfully converted values
print(f"\nAverage price (ignoring NaN): ${messy_prices['Price'].mean():.2f}")

**What Happened:** "Call" couldn't convert, so it became NaN. Much better than crashing. Now we know which items have problems and can decide how to handle them.

### Exercise 5: Type Validation and Conversion

Given product data with various type problems:
1. Check the current data types and identify problems
2. Convert Price to numeric type, handling $ symbols and errors gracefully
3. Convert Quantity to integer type
4. Identify which products had price conversion failures
5. Fill failed price conversions with the median of successful conversions
6. Calculate total inventory value (Price × Quantity)

In [ ]:
# Given: Product data with type problems
products = pd.DataFrame({
    'Product': ['Widget', 'Gadget', 'Tool', 'Item', 'Device'],
    'Price': ['$19.99', '29.99', 'Call', '$24.99', '34.99'],
    'Quantity': ['100', '50', '75', '80', '60']
})

print("Product data with type issues:")
print(products)
print("\nCurrent types:")
print(products.dtypes)

# Your code here - complete all six tasks


In [ ]:
# Solution
products_fixed = products.copy()

# 1. Problems: Price has $ and non-numeric, Quantity is strings
print("Type problems identified:")
print("- Price column contains $ symbols and 'Call' text")
print("- Quantity column is stored as strings\n")

# 2. Convert Price, removing $ symbols first, then safe conversion
products_fixed['Price'] = products_fixed['Price'].str.replace('$', '')
products_fixed['Price'] = pd.to_numeric(
    products_fixed['Price'], errors='coerce'
)

# 3. Convert Quantity to int
products_fixed['Quantity'] = products_fixed['Quantity'].astype(int)

print("After type conversion:")
print(products_fixed)

# 4. Identify failed conversions
failed_mask = products_fixed['Price'].isna()
print("\nProducts with price conversion failures:")
print(products_fixed[failed_mask])

# 5. Fill failed prices with median
price_median = products_fixed['Price'].median()
products_fixed['Price'] = products_fixed['Price'].fillna(price_median)
print(f"\nFilled failed prices with median: ${price_median:.2f}")

# 6. Calculate inventory value
products_fixed['Value'] = products_fixed['Price'] * products_fixed['Quantity']
total_value = products_fixed['Value'].sum()
print("\nFinal product data with inventory value:")
print(products_fixed)
print(f"\nTotal inventory value: ${total_value:.2f}")

**Solution Explanation:** Removed $ symbols, used safe conversion ("Call" became NaN), converted Quantity to int, filled failed prices with median ($27.49), calculated inventory value ($9,797.50). This demonstrates the complete type validation workflow.

## Part 7: Renaming Columns and Complete Workflow

### Standardizing Column Names

Column names should be clear, consistent, and easy to work with in code. Real datasets often have messy names with spaces, inconsistent capitalization, cryptic abbreviations, or special characters. The most common Python convention is snake_case: lowercase words separated by underscores. This makes code cleaner and less error-prone.

In [ ]:
# Dataset with messy column names (typical after Excel export)
messy_cols = pd.DataFrame({
    'Student Name': ['Alice', 'Bob', 'Charlie'],
    'test_score': [87, 92, 88],
    'FinalGrade': [90, 88, 91],
    'E-Mail': ['alice@edu', 'bob@edu', 'charlie@edu']
})

print("Original column names (inconsistent):")
print(messy_cols.columns.tolist())
print("\nData:")
print(messy_cols)

In [ ]:
# Rename columns to consistent snake_case format
standardized = messy_cols.rename(columns={
    'Student Name': 'student_name',
    'test_score': 'test_score',      # Already good
    'FinalGrade': 'final_grade',
    'E-Mail': 'email'
})

print("Standardized column names (snake_case):")
print(standardized.columns.tolist())
print("\nData with clean column names:")
print(standardized)

**What Happened:** All columns now follow snake_case: lowercase with underscores, no spaces, no special characters. This makes code cleaner and prevents errors.

### Exercise 6: Complete Data Cleaning Workflow

Apply the complete workflow to messy employee data:
1. Inspect the data and identify all quality issues
2. Remove duplicate employees based on EmployeeID
3. Convert Salary from string to numeric (handle $ and commas)
4. Handle missing Departments by filling with "Unassigned"
5. Handle missing Salaries by filling with the median
6. Standardize column names to snake_case
7. Calculate total payroll from cleaned data

In [ ]:
# Given: Messy employee data
employees = pd.DataFrame({
    'Employee Name': ['Alice', 'Bob', 'Charlie', 'Alice', 'Diana'],
    'EmployeeID': [1001, 1002, 1003, 1001, 1004],
    'Department': ['Sales', 'IT', np.nan, 'Sales', 'HR'],
    'Salary': ['$50,000', '$75,000', 'Not Set', '$50,000', np.nan]
})

print("Original messy employee data:")
print(employees)

# Your code here - follow the complete workflow


In [ ]:
# Solution - Complete Workflow
print("STEP 1: IDENTIFY ISSUES")
print(f"Duplicates: {employees.duplicated(subset=['EmployeeID']).sum()}")
print(f"Missing Departments: {employees['Department'].isna().sum()}")
print(f"Salary format issues: Contains $, commas, and 'Not Set'\n")

# Step 2: Remove duplicates
clean_employees = employees.drop_duplicates(
    subset=['EmployeeID'], keep='first'
)
print(f"STEP 2: After removing duplicates: {len(clean_employees)} rows\n")

# Step 3: Convert Salary to numeric
clean_employees['Salary'] = clean_employees['Salary'].str.replace(
    '$', ''
).str.replace(',', '')
clean_employees['Salary'] = pd.to_numeric(
    clean_employees['Salary'], errors='coerce'
)
print("STEP 3: Converted Salary to numeric\n")

# Step 4: Fill missing Departments
clean_employees['Department'] = clean_employees['Department'].fillna(
    'Unassigned'
)
print("STEP 4: Filled missing Departments with 'Unassigned'\n")

# Step 5: Fill missing Salaries with median
salary_median = clean_employees['Salary'].median()
clean_employees['Salary'] = clean_employees['Salary'].fillna(
    salary_median
)
print(f"STEP 5: Filled missing Salaries with median: ${salary_median:,.2f}\n")

# Step 6: Standardize column names
clean_employees = clean_employees.rename(columns={
    'Employee Name': 'employee_name',
    'EmployeeID': 'employee_id',
    'Department': 'department',
    'Salary': 'salary'
})
print("STEP 6: Standardized column names\n")

# Step 7: Calculate total payroll
print("FINAL CLEANED DATA:")
print(clean_employees)
total_payroll = clean_employees['salary'].sum()
print(f"\nTotal annual payroll: ${total_payroll:,.2f}")
print(f"Average salary: ${clean_employees['salary'].mean():,.2f}")

**Solution Explanation:** Successfully cleaned through systematic workflow: removed duplicate, converted salaries, filled missing values appropriately, standardized names. Final dataset has 4 clean employee records. Total payroll: $237,500, average salary: $59,375.

## Summary and Key Takeaways

### What You Learned

You mastered fundamental data cleaning techniques:

1. **Missing Data Detection:** Use `isna()`, `notna()`, and `info()` to identify missing data
2. **Missing Data Removal:** Use `dropna()` with parameters (how='all', subset=[])
3. **Missing Data Filling:** Use `fillna()` with appropriate strategies (mean/median, constants, forward/backward)
4. **Duplicate Detection:** Use `duplicated()` and `drop_duplicates()` with `subset` parameter
5. **Type Validation:** Check with `dtypes`, convert with `astype()` or `to_numeric(errors='coerce')`
6. **Column Standardization:** Use `rename()` for consistent snake_case naming
7. **Systematic Workflow:** Follow Detect → Assess → Clean → Verify pattern

### Best Practices

- Always detect before acting - quantify problems first
- Choose strategies based on context - mean vs median, drop vs fill
- Use subset parameters for key columns
- Verify after cleaning - check operations worked correctly
- Document decisions for future reference

### Next Steps

In Lecture 19, we'll advance to reading data from files (CSV, Excel), combining DataFrames with merge/join, grouping with groupby(), and reshaping with pivot tables. Data cleaning skills are the foundation for these advanced operations.